## 2 Ground Control Stations (simple)

This is a first version. The two ground control stations are working in series. 

In [1]:
from helpers import local2global, kill_processes,clean
from simulators import Simulator, Gazebo, ConfigGazebo, QGC
from plan import Plan
from helpers.change_coordinates import Offset
from config import Color
kill_processes()

In [2]:
# import random
# from helpers.change_coordinates import Offset
# n_vehicles = 10
# offsets = [
#         (
#             random.uniform(-5, 5),  # east
#             random.uniform(-5, 5),  # north
#             0,                          # up
#             random.randint(0, 359)      # heading
#         )
#         for _ in range(n_vehicles)
#     ]
# offsets

## Create Plans

In [ ]:
offsets: list[Offset] = [
    (0, 0, 0, 0),
    (4.272452965244035, -2.0624885894963674, 0, 308),
    (3.0267596011325804, 2.2013367285195207, 0, 21),
]
n_vehicles = len(offsets)

# offsets = [  # east, north, up, heading
#     (5., 5., 0., 90.),
#     (10., 0., 0., 45.),
#     (-5., -10., 0., 225.),
#     (-15., 0., 0., 0.),
#     (0., -20., 0., 0.),
# ]



local_paths = [Plan.create_square_path(side_len=8, alt=5) for _ in range(n_vehicles)]
plans = [Plan.basic(wps=path, wp_margin=0.5) for path in local_paths]
homes = [offset[:3] for offset in offsets]

## Visualization Parameters

In [4]:
n_blue_veh = 2
global_paths = [local2global(path, home) for path, home in zip(local_paths, homes)]
models = n_blue_veh*[('iris',Color.BLUE)]+(n_vehicles-n_blue_veh)*[('iris',Color.GREEN)]   # must agree with n_vehicles
markers = [ConfigGazebo.create_trajectory_from_array(array=global_paths[i],color=models[i][1]) for i in range(n_vehicles)]
Gazebo.plot_3d_interactive(markers=markers, title="Simulation Markers", frames=(0.2, 0.2, 0.6), ground=-0.05)


## Choose Simulator

In [5]:
simulator = QGC(offsets=offsets, plans=plans, origin=(-35.3633245, 149.1652241, 0, 0))

simulator = Simulator(offsets=offsets, plans=plans)

gazebo_config = ConfigGazebo(world_path="simulators/gazebo/worlds/runway.world",models=models,markers = markers)
simulator = Gazebo(offsets=offsets,plans=plans,config=gazebo_config)


Launch Simulator

In [ ]:
sysids = list(range(1,n_vehicles+1))
orac,gcss = simulator.launch(gcs_sysids={'blue GCS 🟦':sysids[:n_blue_veh],'green GCS 🟩':sysids[n_blue_veh:]})
blue_gcs,green_gcs=gcss
while len(orac.conns):
    blue_gcs.gather_broadcasts()
    green_gcs.gather_broadcasts()
    blue_gcs.save_pos()
    green_gcs.save_pos() 
    for sysid in list(orac.conns.keys()):
        if orac.is_plan_done(sysid):
            orac.remove(sysid)
clean()

🖥️ Gazebo launched for 3D simulation.
🚀 Vehicle 1 launched (PID 211979)
🚀 Vehicle 1 logic launched (PID 211980)
🔗 UAV logic 1 is connected to Oracle ⚪
🔗 UAV logic 1 is connected to blue 🟦
🚀 Vehicle 2 launched (PID 213245)
🚀 Vehicle 2 logic launched (PID 213246)
🔗 UAV logic 2 is connected to Oracle ⚪
🔗 UAV logic 2 is connected to blue 🟦
🚀 Vehicle 3 launched (PID 213413)
🚀 Vehicle 3 logic launched (PID 213414)
🔗 UAV logic 3 is connected to Oracle ⚪
🔗 UAV logic 3 is connected to green 🟩
✅ Vehicle 1 terminated
✅ Vehicle 2 terminated
✅ Vehicle 3 terminated


## Print Positions gathered

In [7]:
import numpy as np
from numpy.typing import NDArray
from typing import List
blue_paths:List[NDArray[np.float64]] = []
for sysid,path in blue_gcs.paths.items():
    blue_paths.append(np.array([x for x in path if x is not None]))

markers = [ConfigGazebo.create_trajectory_from_array(array=path,color=Color.BLUE) for path in blue_paths]
Gazebo.plot_3d_interactive(markers=markers,title="Simulation Waypoints",frames=(0.2, 0.2, 0.6),ground=-0.05)

In [8]:
green_paths = []
for sysid,path in green_gcs.paths.items():
    green_paths.append(np.array([x for x in path if x is not None]))

markers = [ConfigGazebo.create_trajectory_from_array(array=path,color=Color.GREEN) for path in green_paths]
Gazebo.plot_3d_interactive(markers=markers,title="Simulation Waypoints",frames=(0.2, 0.2, 0.6),ground=-0.05)